# Bi-LSTM Emotion Classification

In [ ]:
!pip install -q wandb huggingface_hub transformers torch scikit-learn pandas numpy

In [ ]:
import os
import numpy as np
import pandas as pd
import torch
import torch.nn as nn
from torch.optim import AdamW
from torch.utils.data import Dataset, DataLoader
from transformers import AutoTokenizer
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score
import wandb
from huggingface_hub import login
from kaggle_secrets import UserSecretsClient

# Secrets
user_secrets = UserSecretsClient()
wandb.login(key=user_secrets.get_secret("wandb_api_key"))
login(token=user_secrets.get_secret("hf_api_key"))

# Config
PROJECT = "emotion-classification-dl"
RUN_NAME = "simple-bilstm-scratch"
MODEL_NAME = "emotion-classifier-bilstm"
LABELS = ["anger", "fear", "joy", "sadness", "surprise"]
MAX_LEN = 100
BATCH_SIZE = 32
EPOCHS = 10
LR = 1e-3
EMBED_DIM = 100
HIDDEN_DIM = 128
DROPOUT = 0.3
DEVICE = torch.device("cuda" if torch.cuda.is_available() else "cpu")

# Seed
torch.manual_seed(42)
np.random.seed(42)

In [ ]:
class EmotionDS(Dataset):
    def __init__(self, df, tokenizer):
        self.texts = df['text'].tolist()
        self.labels = df[LABELS].values.astype(np.float32)
        self.tokenizer = tokenizer

    def __len__(self): return len(self.texts)

    def __getitem__(self, idx):
        enc = self.tokenizer(self.texts[idx], truncation=True, padding='max_length', max_length=MAX_LEN, return_tensors='pt')
        return {
            'input_ids': enc['input_ids'].squeeze(0),
            'labels': torch.tensor(self.labels[idx])
        }

class BiLSTM(nn.Module):
    def __init__(self, vocab_size):
        super().__init__()
        self.embedding = nn.Embedding(vocab_size, EMBED_DIM)
        self.lstm = nn.LSTM(EMBED_DIM, HIDDEN_DIM, batch_first=True, bidirectional=True, dropout=DROPOUT, num_layers=2)
        self.fc = nn.Linear(HIDDEN_DIM * 2, len(LABELS))
        
    def forward(self, x):
        x = self.embedding(x)
        _, (hidden, _) = self.lstm(x)
        # Concat forward and backward hidden states from last layer
        x = torch.cat((hidden[-2], hidden[-1]), dim=1)
        return self.fc(x)

In [ ]:
def train():
    # Data
    df = pd.read_csv("/kaggle/input/2025-sep-dl-gen-ai-project/train.csv")
    if "text" not in df.columns: df = df.rename(columns={"comment_text": "text"}) # Handle column name
    
    train_df, val_df = train_test_split(df, test_size=0.2, random_state=42)
    tokenizer = AutoTokenizer.from_pretrained("bert-base-uncased")
    
    train_loader = DataLoader(EmotionDS(train_df, tokenizer), batch_size=BATCH_SIZE, shuffle=True)
    val_loader = DataLoader(EmotionDS(val_df, tokenizer), batch_size=BATCH_SIZE)
    
    # Model
    model = BiLSTM(tokenizer.vocab_size).to(DEVICE)
    optimizer = AdamW(model.parameters(), lr=LR)
    criterion = nn.BCEWithLogitsLoss()
    
    # WandB
    wandb.init(project=PROJECT, name=RUN_NAME)
    
    best_f1 = 0
    for epoch in range(EPOCHS):
        model.train()
        train_loss = 0
        for batch in train_loader:
            optimizer.zero_grad()
            loss = criterion(model(batch['input_ids'].to(DEVICE)), batch['labels'].to(DEVICE))
            loss.backward()
            optimizer.step()
            train_loss += loss.item()
            
        # Validation
        model.eval()
        preds, targets = [], []
        with torch.no_grad():
            for batch in val_loader:
                logits = model(batch['input_ids'].to(DEVICE))
                preds.append(torch.sigmoid(logits).cpu().numpy())
                targets.append(batch['labels'].cpu().numpy())
        
        preds = np.vstack(preds)
        targets = np.vstack(targets)
        f1 = f1_score(targets, (preds >= 0.5).astype(int), average='macro')
        
        print(f"Epoch {epoch+1}: Loss {train_loss/len(train_loader):.4f}, Val F1 {f1:.4f}")
        wandb.log({"loss": train_loss/len(train_loader), "val_f1": f1})
        
        if f1 > best_f1:
            best_f1 = f1
            torch.save(model.state_dict(), "model.pth")
            
    wandb.finish()
    return best_f1

if os.path.exists("/kaggle/input/2025-sep-dl-gen-ai-project/train.csv"):
    train()

In [ ]:
# Upload
if os.path.exists("model.pth"):
    api = HfApi()
    repo_id = f"{api.whoami()['name']}/{MODEL_NAME}"
    create_repo(repo_id, exist_ok=True)
    api.upload_file(path_or_fileobj="model.pth", path_in_repo="pytorch_model.bin", repo_id=repo_id)
    print(f"Uploaded to https://huggingface.co/{repo_id}")